In [1]:
## Import packages
import numpy as np
import pandas as pd
import copy
# from sklearn.preprocessing import StandardScaler

from sklearn.preprocessing import StandardScaler, LabelEncoder, LabelBinarizer


import matplotlib.pyplot as plt
import seaborn as sns

plt.style.use('ggplot')

In [2]:
train = pd.read_csv('train.csv/train.csv')
train.head()

id                                              title              author  \
0   0  House Dem Aide: We Didn’t Even See Comey’s Let...       Darrell Lucus   
1   1  FLYNN: Hillary Clinton, Big Woman on Campus - ...     Daniel J. Flynn   
2   2                  Why the Truth Might Get You Fired  Consortiumnews.com   
3   3  15 Civilians Killed In Single US Airstrike Hav...     Jessica Purkiss   
4   4  Iranian woman jailed for fictional unpublished...      Howard Portnoy   

                                                text  label  
0  House Dem Aide: We Didn’t Even See Comey’s Let...      1  
1  Ever get the feeling your life circles the rou...      0  
2  Why the Truth Might Get You Fired October 29, ...      1  
3  Videos 15 Civilians Killed In Single US Airstr...      1  
4  Print \nAn Iranian woman has been sentenced to...      1

In [3]:
train.shape

(20800, 5)

In [ ]:
train.dtypes

In [4]:
test = pd.read_csv('test.csv/test.csv')
test.shape

(5200, 4)

In [5]:
submit = pd.read_csv('submit.csv')

In [6]:
submit

id  label
0     20800      0
1     20801      1
2     20802      0
3     20803      1
4     20804      1
...     ...    ...
5195  25995      0
5196  25996      1
5197  25997      0
5198  25998      1
5199  25999      0

[5200 rows x 2 columns]

In [7]:
test.head()

id                                              title  \
0  20800  Specter of Trump Loosens Tongues, if Not Purse...   
1  20801  Russian warships ready to strike terrorists ne...   
2  20802  #NoDAPL: Native American Leaders Vow to Stay A...   
3  20803  Tim Tebow Will Attempt Another Comeback, This ...   
4  20804                    Keiser Report: Meme Wars (E995)   

                    author                                               text  
0         David Streitfeld  PALO ALTO, Calif.  —   After years of scorning...  
1                      NaN  Russian warships ready to strike terrorists ne...  
2            Common Dreams  Videos #NoDAPL: Native American Leaders Vow to...  
3            Daniel Victor  If at first you don’t succeed, try a different...  
4  Truth Broadcast Network  42 mins ago 1 Views 0 Comments 0 Likes 'For th...

In [8]:
test.dtypes

id         int64
title     object
author    object
text      object
dtype: object

In [9]:
test.isna().sum().sort_values(ascending = False)

author    503
title     122
text        7
id          0
dtype: int64

In [10]:
# make a copy of the dataframe in case 
#train_original = copy.deepcopy(train)

In [11]:
train["label"].value_counts()


#see distribution of 1 and 0 labels 

1    10413
0    10387
Name: label, dtype: int64

In [12]:
train.isna().sum().sort_values(ascending = False)

author    1957
title      558
text        39
label        0
id           0
dtype: int64

In [23]:
import pandas as pd
import seaborn as sns
import nltk, math
import csv, sys
#from nltk.sentiment.vader import SentimentIntensityAnalyzer
from vaderSentiment.vaderSentiment import SentimentIntensityAnalyzer

train_copy = train.copy()


analyzer = SentimentIntensityAnalyzer()


train_copy['compound'] = [analyzer.polarity_scores(v)['compound'] for v in train_copy['text']]
train_copy['neg'] = [analyzer.polarity_scores(v)['neg'] for v in train_copy['text']]
train_copy['neu'] = [analyzer.polarity_scores(v)['neu'] for v in train_copy['text']]
train_copy['pos'] = [analyzer.polarity_scores(v)['pos'] for v in train_copy['text']]






# Text pre processing 

In [13]:
# basic pre-processing
from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize
from nltk.stem import PorterStemmer
import re

from wordcloud import WordCloud

In [14]:
#train["title"] = train["title"].astype(str)
#train["text"] = train["text"].astype(str)
#train = train.dropna(subset=['title', 'text'])
train = train.fillna(' ')
#test = test.dropna(subset=['title', 'text'])
#train.dropna(axis=0).shape
#train.dropna(axis=1).shape

In [15]:
train.shape

(20800, 5)

In [16]:
test.shape

(5200, 4)

In [17]:
#train = train.transpose
topwords_dict = {}
for i in train.text:
    top = train["text"].sort_values(ascending=False).head(1)
    topwords_dict["text"]= list(zip(top.index, top.values))

#topwords_dict

In [ ]:
#for i, top_words in topwords_dict.items():
    #print(i)
    #print(', '.join([str(i) for i in top_words[0:14]]))
    #print('---')

In [18]:
from collections import Counter

# extracting words
words = []
for i in train.columns:
    top = [word for word in topwords_dict["text"]]
    for t in top:
        words.append(t)
        
#words

In [ ]:
#Counter(words).most_common()


In [19]:
# basic pre-processing
from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize
from nltk.stem import WordNetLemmatizer
import re

stop_words = set(stopwords.words('english'))
#stemmer = PorterStemmer()


#remove stop words 
#lemmetization instead of stemmer 

lemmatizer = WordNetLemmatizer()

#def preprocess(review):
 #   review = " ".join([stemmer.stem(w.lower()) for w in word_tokenize(re.sub('[^a-zA-Z]+', ' ', review.replace("<br />", ""))) if not w in stop_words])
  #  return review
def preprocess(train):
    text = train.lower()
    text = re.sub('\[.*?\]', '', text) # remove square brackets
    text = re.sub(r'[^\w\s]','',text) # remove punctuation
    text = re.sub('\w*\d\w*', '', text) # remove words containing numbers
    text = re.sub(r'http\S+', '', text)
    text = re.sub('\n', '', text)
    train = ' '.join([lemmatizer.lemmatize(w) for w in word_tokenize(text.replace("<br />", "")) if not w in stop_words])
    return train
     

#cleaning all text from both test and train set 
train['text_clean'] = train.apply(lambda x: preprocess(x['text']), axis=1)
# test['text_clean'] = test.apply(lambda x: preprocess(x['text']), axis=1) 

train.head(10)

#train.isna().sum()

id                                              title  \
0   0  House Dem Aide: We Didn’t Even See Comey’s Let...   
1   1  FLYNN: Hillary Clinton, Big Woman on Campus - ...   
2   2                  Why the Truth Might Get You Fired   
3   3  15 Civilians Killed In Single US Airstrike Hav...   
4   4  Iranian woman jailed for fictional unpublished...   
5   5  Jackie Mason: Hollywood Would Love Trump if He...   
6   6  Life: Life Of Luxury: Elton John’s 6 Favorite ...   
7   7  Benoît Hamon Wins French Socialist Party’s Pre...   
8   8  Excerpts From a Draft Script for Donald Trump’...   
9   9  A Back-Channel Plan for Ukraine and Russia, Co...   

                         author  \
0                 Darrell Lucus   
1               Daniel J. Flynn   
2            Consortiumnews.com   
3               Jessica Purkiss   
4                Howard Portnoy   
5               Daniel Nussbaum   
6                                 
7               Alissa J. Rubin   
8                                 
9  Megan Twohey and Scott Shane   

                                                text  label  \
0  House Dem Aide: We Didn’t Even See Comey’s Let...      1   
1  Ever get the feeling your life circles the rou...      0   
2  Why the Truth Might Get You Fired October 29, ...      1   
3  Videos 15 Civilians Killed In Single US Airstr...      1   
4  Print \nAn Iranian woman has been sentenced to...      1   
5  In these trying times, Jackie Mason is the Voi...      0   
6  Ever wonder how Britain’s most iconic pop pian...      1   
7  PARIS  —   France chose an idealistic, traditi...      0   
8  Donald J. Trump is scheduled to make a highly ...      0   
9  A week before Michael T. Flynn resigned as nat...      0   

                                          text_clean  
0  house dem aide didnt even see comeys letter ja...  
1  ever get feeling life circle roundabout rather...  
2  truth might get fired october tension intellig...  
3  video civilian killed single u airstrike ident...  
4  print iranian woman sentenced six year prison ...  
5  trying time jackie mason voice reason could wi...  
6  ever wonder britain iconic pop pianist get lon...  
7  paris france chose idealistic traditional cand...  
8  donald j trump scheduled make highly anticipat...  
9  week michael flynn resigned national security ...

In [20]:
from sklearn.feature_extraction.text import TfidfVectorizer

# split dataset to training and test dataset
from sklearn.feature_extraction.text import CountVectorizer #one hot 
from sklearn.model_selection import train_test_split


data_train, data_val, y_train, y_val = train_test_split(train['text_clean'], train['label'], 
                                                          test_size = 0.25, random_state = 2020, stratify = train['label'])

c_vectorizer = CountVectorizer()
train_counts = c_vectorizer.fit_transform(data_train)
val_counts = c_vectorizer.transform(data_val)

#
c_vectorizer.get_feature_names()
c_vectorizer.transform(data_train).toarray()


tfid_vectorizer = TfidfVectorizer()
train_vectors = tfid_vectorizer.fit_transform(data_train)
test_vectors = tfid_vectorizer.transform(data_val)

#
tfid_vectorizer.get_feature_names()
tfid_vectorizer.transform(data_train).toarray()

#tfid_review = pd.DataFrame(data = tfid_vectorizer.transform(data_train).toarray(), index = dataset.index)
#tfid_review.columns = tfid_vectorizer.get_feature_names()
#tfid_review.head()


array([[0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       ...,
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.]])

In [22]:
from textblob import TextBlob
import plotly.express as px

desc_blob = [TextBlob(desc) for desc in train['text_clean']]
#add the sentiment metrics to the dataframe
train['Polarity'] = [b.sentiment.polarity for b in desc_blob]
train['Subjectivity'] = [b.sentiment.subjectivity for b in desc_blob]

#train.head(3)

def Sentiscore(score):
    if score <0:
        return 'Negative'
    elif score == 0:
        return 'Neutral'
    else:
        return 'Positive'
    
train['category'] = train['Polarity'].apply(Sentiscore)

fig = px.scatter(train, 
                 x='Polarity', 
                 y='Subjectivity', 
                 color = 'category',
                 size='Subjectivity',
                 hover_name= 'author')
fig.show()

fig = px.strip(train, x="Polarity", y="Subjectivity", 
               orientation="h", 
               color="category",
               hover_name= 'author')



fig.show()




In [25]:
#train.to_csv(r'C:\Desktop\cleaneddata.csv')